In [1]:
import nltk
import torch
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from hdbscan import HDBSCAN
import pandas as pd
from textblob import TextBlob
from collections import defaultdict

import json
import csv
from pymongo import MongoClient


In [2]:

from pytorch_pretrained_bert import BertTokenizer, BertModel, BertForMaskedLM
from transformers import BertTokenizer as bt

import numpy as np

from transformers import BertTokenizer, BertModel


/Users/daniel/opinio-services/opinio_env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
import gensim
from gensim import corpora, models

In [4]:

from nltk.tokenize import word_tokenize
from collections import Counter
import re



In [5]:
# Download NLTK resources if needed
nltk.download('punkt')
nltk.download('stopwords')


[nltk_data] Downloading package punkt to /Users/daniel/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/daniel/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [7]:


# Load BERT model
bert_model = BertModel.from_pretrained('bert-base-uncased')
bert_model.eval()

# Load reviews from a CSV file
# TODO: Make this dynamic
df1 = pd.read_csv('DATA/sentiment_reviews_withcount.csv')
reviews = df1['review_text'].tolist()  # Replace 'review_text' with your column name if different


In [8]:

# Preprocess reviews: Tokenization, removing stopwords, non-alphabetical characters
def preprocess_text(texts):
    stop_words = set(stopwords.words('english'))
    preprocessed_texts = [
        [word for word in word_tokenize(document.lower()) if word.isalpha() and word not in stop_words]
        for document in texts]
    return preprocessed_texts


preprocessed_reviews = preprocess_text(reviews)


In [9]:

# Create a dictionary and corpus for LDA
dictionary = corpora.Dictionary(preprocessed_reviews)
corpus = [dictionary.doc2bow(text) for text in preprocessed_reviews]

# Apply LDA
num_topics = 5  # Adjust based on your data and needs
lda_model = models.LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics, random_state=42, passes=15,
                            iterations=100)

# Additional stopwords for category refinement
additional_stopwords = {'get', 'great', 'like', 'really', 'good', 'gym', 'place', 'love', 'hate', 'one', 'trainer'}  # Add more words as needed



In [10]:


def preprocess_text(text):
    stop_words = stopwords.words('english')
    text = text.lower()  # Convert to lowercase
    words = [word for word in text.split() if word not in stop_words]
    # Stemming (uncomment if desired)
    # words = [stemmer.stem(word) for word in words]
    return " ".join(words)


def get_bert_embeddings(sentences):
    # Tokenize sentences
    tokenized_sentences = tokenizer(sentences, padding=True, truncation=True, return_tensors='pt')

    # Get BERT embeddings
    with torch.no_grad():
        outputs = bert_model(**tokenized_sentences)
        embeddings = outputs.last_hidden_state.mean(dim=1)

    return embeddings

def calculate_center(df):
    centers = {}
    for cluster in df['Cluster'].unique():
        cluster_embeddings = df[df['Cluster'] == cluster]['bert_embeddings']
        center = cluster_embeddings.apply(pd.Series)
        center = center.mean()
        centers[cluster] = center.tolist()
    return centers


def find_closest_sentence(df, centers):
    closest_sentences = {}
    for cluster, center in centers.items():
        distances = [np.linalg.norm(np.pad(embedding, (0, len(center) - len(embedding)), 'constant') - center)
                        for
                        embedding in df[df['Cluster'] == cluster]['Vector'].values]
        closest_index = distances.index(min(distances))
        closest_sentences[cluster] = df[df['Cluster'] == cluster]['Sentences'].values[closest_index]
    return closest_sentences


def get_combined_categories(ldamodel, num_topics, num_keywords=5):
    # Collect all words from all topics
    all_keywords = []
    for i in range(num_topics):
        topic_terms = ldamodel.show_topic(i)
        all_keywords.extend([word for word, _ in topic_terms])

    # Count the frequency of each word
    keyword_counts = Counter(all_keywords)

    # Filter out additional stopwords
    filtered_keywords = {word: count for word, count in keyword_counts.items() if word not in additional_stopwords}

    # Get the most common words across all topics, after filtering
    most_common_keywords = [word for word, count in Counter(filtered_keywords).most_common(num_keywords)]
    return most_common_keywords



In [11]:

#review data type -- sentiment empty
# -->

# Sample gym reviews
#reviews = [
    #"The staff at this gym are incredibly friendly and helpful. They always go the extra mile to make sure I have a great workout experience.",
    #"The equipment is top-notch and well-maintained. They have a wide variety of machines for all my training needs.",
   # "The gym is always clean and well-organized. It's a pleasure to work out in such a pleasant environment.",
  #  "The staff could be a bit more attentive, but the equipment is good overall.",
 #   "This gym is a bit dirty at times, but the staff is friendly and the classes are great.",
#]

df = pd.DataFrame(reviews, columns=['Sentences'])

# Define your labels
labels = get_combined_categories(lda_model, num_topics)

# Preprocess reviews
processed_reviews = [preprocess_text(review) for review in reviews]
df['processed_sentences'] = processed_reviews


label_tracker_dict = {}



In [12]:
# REVIEWS ARE PROCESSED WITH LABELS
labels
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  
0    used work absolutely loved time. wonderful ful...  
1    facility small number people trying serve. enf...  
2    super friendly gym yet crowded 5:30 pm. also w...  
3    always amazing. using facility many years sinc...  
4    joined really impressed cleanliness pool! swim...  
..                                                 ...  
231  services rules bad .i called stop charging wee...  
232  tour. place looks good, small. change rooms od...  
233  handsdown best gym ever joined. array great cl...  
234  used work found king cut fitness! way better r...  
235  signed goodlife three months ago hoping get ba...  

[236 rows x 2 columns]

In [13]:

for i in range(0,len(labels)):
    label_tracker_dict[i] = labels[i]

# Convert labels to text for feature representation
label_texts = [" ".join([label, "review is"]) for label in labels]

# Feature engineering with TF-IDF

tokenizer = bt.from_pretrained('bert-base-uncased')
# Get BERT embeddings for sentences
embeddings = get_bert_embeddings(processed_reviews)
label_embeddings = get_bert_embeddings(label_texts)
# Save embeddings to DataFrame
df['bert_embeddings'] = embeddings.tolist()



In [14]:
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  \
0    used work absolutely loved time. wonderful ful...   
1    facility small number people trying serve. enf...   
2    super friendly gym yet crowded 5:30 pm. also w...   
3    always amazing. using facility many years sinc...   
4    joined really impressed cleanliness pool! swim...   
..                                                 ...   
231  services rules bad .i called stop charging wee...   
232  tour. place looks good, small. change rooms od...   
233  handsdown best gym ever joined. array great cl...   
234  used work found king cut fitness! way better r...   
235  signed goodlife three months ago hoping get ba...   

                                       bert_embeddings  
0    [0.32818377017974854, -0.22182533144950867, 0....  
1    [0.1721685826778412, -0.04415113478899002, 0.1...  
2    [0.25516438484191895, -0.31639814376831055, 0....  
3    [-0.04373439401388168, -0.3006299138069153, 0....  
4    [0.22954954206943512, -0.5347655415534973, 0.5...  
..                                                 ...  
231  [0.24488377571105957, -0.1701994091272354, 0.6...  
232  [0.08404839783906937, -0.26631253957748413, 0....  
233  [0.19301766157150269, -0.07032106816768646, 0....  
234  [0.07691993564367294, -0.42288994789123535, 0....  
235  [0.16002558171749115, -0.2914293110370636, 0.6...  

[236 rows x 3 columns]

In [17]:


# HDBSCAN clustering
clusterer = HDBSCAN(min_cluster_size=2,  # Allow any cluster size
                             min_samples=2,         # Ensure exactly three clusters
                             metric='euclidean',
                             cluster_selection_method='leaf', # Choose 'eom' to automatically select the number of clusters
                             prediction_data=True)
  # Adjust parameters as needed
clusterer.fit(embeddings)

# Cluster centroids
cluster_labels = clusterer.labels_

df['Cluster'] = cluster_labels

centers = calculate_center(df)



In [18]:
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  \
0    used work absolutely loved time. wonderful ful...   
1    facility small number people trying serve. enf...   
2    super friendly gym yet crowded 5:30 pm. also w...   
3    always amazing. using facility many years sinc...   
4    joined really impressed cleanliness pool! swim...   
..                                                 ...   
231  services rules bad .i called stop charging wee...   
232  tour. place looks good, small. change rooms od...   
233  handsdown best gym ever joined. array great cl...   
234  used work found king cut fitness! way better r...   
235  signed goodlife three months ago hoping get ba...   

                                       bert_embeddings  cluster  Cluster  
0    [0.32818377017974854, -0.22182533144950867, 0....       -1       -1  
1    [0.1721685826778412, -0.04415113478899002, 0.1...       -1       -1  
2    [0.25516438484191895, -0.31639814376831055, 0....       -1       -1  
3    [-0.04373439401388168, -0.3006299138069153, 0....       -1       -1  
4    [0.22954954206943512, -0.5347655415534973, 0.5...       -1       -1  
..                                                 ...      ...      ...  
231  [0.24488377571105957, -0.1701994091272354, 0.6...       -1       -1  
232  [0.08404839783906937, -0.26631253957748413, 0....       -1       -1  
233  [0.19301766157150269, -0.07032106816768646, 0....       -1       -1  
234  [0.07691993564367294, -0.42288994789123535, 0....       -1       -1  
235  [0.16002558171749115, -0.2914293110370636, 0.6...       -1       -1  

[236 rows x 5 columns]

In [19]:
# CLUSTERING 

# Cosine similarity with threshold -- fix cluster centroid here
threshold = 0.62 # Adjust as needed
assigned_labels = {}
for cluster_id in centers.keys():
    centroid = centers[cluster_id]
    if cluster_id == -1:
        assigned_labels[cluster_id] = [-1]
        continue
    centroid = pd.Series(centroid)
    assigned_labels[cluster_id] = []
    for label_id, label_vector in enumerate(label_embeddings):
        label_vector = pd.Series(label_vector)
        similarity = cosine_similarity(centroid.values.reshape(1, -1), label_vector.values.reshape(1, -1))[0][0]
        if similarity > threshold:
            curr_labels = assigned_labels[cluster_id]
            curr_labels.append(label_id)
            assigned_labels[cluster_id] = curr_labels

for cluster_id in centers.keys():
    if (len(assigned_labels[cluster_id]) == 0):
        centroid = centers[cluster_id]
        if (assigned_labels[cluster_id] == [-1]):
            continue
        centroid = pd.Series(centroid)
        maximum = -1
        for label_id, label_vector in enumerate(label_embeddings):
            label_vector = pd.Series(label_vector)
            similarity = cosine_similarity(centroid.values.reshape(1, -1), label_vector.values.reshape(1, -1))[0][0]
            if similarity > maximum:
                assigned_labels[cluster_id] = [label_id]
                maximum = similarity


# assign labels to all sentences seperately who are in cluster -1:

for i in range(0, len(processed_reviews)):
    if df['Cluster'][i] == -1:
        maximum = -1
        for label_id, label_vector in enumerate(label_embeddings):
            label_vector = pd.Series(label_vector)
            similarity = cosine_similarity(embeddings[i].reshape(1, -1), label_vector.values.reshape(1, -1))[0][0]
            if similarity > maximum:
                df['Cluster'][i] = label_id
                maximum = similarity


/var/folders/p4/wjmmpqkj5h1glp_39s3fry100000gn/T/ipykernel_71134/1852618005.py:45: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df['Cluster'][i] = label_id
/var/folders/p4/wjmmpqkj5h1glp_39s3fry100000gn/T/ipykernel_71134/1852618005.py:45: S

In [20]:
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  \
0    used work absolutely loved time. wonderful ful...   
1    facility small number people trying serve. enf...   
2    super friendly gym yet crowded 5:30 pm. also w...   
3    always amazing. using facility many years sinc...   
4    joined really impressed cleanliness pool! swim...   
..                                                 ...   
231  services rules bad .i called stop charging wee...   
232  tour. place looks good, small. change rooms od...   
233  handsdown best gym ever joined. array great cl...   
234  used work found king cut fitness! way better r...   
235  signed goodlife three months ago hoping get ba...   

                                       bert_embeddings  cluster  Cluster  
0    [0.32818377017974854, -0.22182533144950867, 0....       -1        1  
1    [0.1721685826778412, -0.04415113478899002, 0.1...       -1        3  
2    [0.25516438484191895, -0.31639814376831055, 0....       -1        1  
3    [-0.04373439401388168, -0.3006299138069153, 0....       -1        1  
4    [0.22954954206943512, -0.5347655415534973, 0.5...       -1        1  
..                                                 ...      ...      ...  
231  [0.24488377571105957, -0.1701994091272354, 0.6...       -1        0  
232  [0.08404839783906937, -0.26631253957748413, 0....       -1        0  
233  [0.19301766157150269, -0.07032106816768646, 0....       -1        1  
234  [0.07691993564367294, -0.42288994789123535, 0....       -1        1  
235  [0.16002558171749115, -0.2914293110370636, 0.6...       -1        2  

[236 rows x 5 columns]

In [21]:



df['assigned_label'] = df['Cluster'].map(assigned_labels)
df['named_labels']  = df['assigned_label'].apply(lambda x: [label_tracker_dict[num] for num in x])
print('breakpoint')


breakpoint


In [22]:
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  \
0    used work absolutely loved time. wonderful ful...   
1    facility small number people trying serve. enf...   
2    super friendly gym yet crowded 5:30 pm. also w...   
3    always amazing. using facility many years sinc...   
4    joined really impressed cleanliness pool! swim...   
..                                                 ...   
231  services rules bad .i called stop charging wee...   
232  tour. place looks good, small. change rooms od...   
233  handsdown best gym ever joined. array great cl...   
234  used work found king cut fitness! way better r...   
235  signed goodlife three months ago hoping get ba...   

                                       bert_embeddings  cluster  Cluster  \
0    [0.32818377017974854, -0.22182533144950867, 0....       -1        1   
1    [0.1721685826778412, -0.04415113478899002, 0.1...       -1        3   
2    [0.25516438484191895, -0.31639814376831055, 0....       -1        1   
3    [-0.04373439401388168, -0.3006299138069153, 0....       -1        1   
4    [0.22954954206943512, -0.5347655415534973, 0.5...       -1        1   
..                                                 ...      ...      ...   
231  [0.24488377571105957, -0.1701994091272354, 0.6...       -1        0   
232  [0.08404839783906937, -0.26631253957748413, 0....       -1        0   
233  [0.19301766157150269, -0.07032106816768646, 0....       -1        1   
234  [0.07691993564367294, -0.42288994789123535, 0....       -1        1   
235  [0.16002558171749115, -0.2914293110370636, 0.6...       -1        2   

    assigned_label named_labels  
0              [2]       [time]  
1              [1]    [classes]  
2              [2]       [time]  
3              [2]       [time]  
4              [2]       [time]  
..             ...          ...  
231            [2]       [time]  
232            [2]       [time]  
233            [2]       [time]  
234            [2]       [time]  
235            [1]    [classes]  

[236 rows x 7 columns]

In [23]:


for i in range(0, len(processed_reviews)):
    for j in labels:
        if j in processed_reviews[i]:
            if j in df['named_labels'][i]:
                continue
            else:
                curr = df['named_labels'][i]
                curr.append(j)
# Print results
print("Reviews:")
for i, review in enumerate(reviews):
    print(f"- Review {i+1}: {review}")

print("\nClusters and assigned labels:")
for cluster_id, labels in assigned_labels.items():
    print(f"- Cluster {cluster_id+1}:", ", ".join(str(labels)))


Reviews:
- Review 1: I used to work here and absolutely loved my time. It's so wonderful you have a full fledged gym, a family development centre and a daycare all in one building. The facility itself for the gym is great because there are a lot of machines you can use as well as good selection of classes to access as well depending on your needs and preference of working out. And for those parents that needed some socialising time could come by the family development centre to either be there with their kids for the programs or drop them off for child minding if they needed to use the gym.
- Review 2: Facility is too small for the number of people it is trying to serve. 
No enforcement of time limits along with people who take 10 minutes between sets using the machines as convenient places to rest while checking their phone messages means a lot of wasted time waiting for machines. 
Broken machines take a long time to repair as do out-of-service lockers in very tight locker rooms. 

No

In [24]:

#import textblob and run it on all the reviews and add a value of sentiment and polarity to the dataframe

sentiments = []
polarities = []
#use the normal reviews
for review in reviews:
    blob = TextBlob(review)
    sentiments.append(blob.sentiment[0] * 2.5 + 2.5)
    polarities.append(blob.sentiment[1]  * 2.5 + 2.5)
#now add to dataframe
df['sentiment'] = sentiments
df['polarity'] = polarities
categories_summaries_sentiments = defaultdict(list)
categores_summaries_polarities = defaultdict(list)
for i in range(0, len(df)):
    for j in df['named_labels'][i]:
        categories_summaries_sentiments[j].append(df['sentiment'][i])
        categores_summaries_polarities[j].append(df['polarity'][i])


df_summaries = pd.DataFrame(columns=['Category', 'Average Sentiment', 'Average Polarity'])
for i in categories_summaries_sentiments.keys():
    #add a row to the dataframe using df.loc
    df_summaries.loc[len(df_summaries)] = [i, sum(categories_summaries_sentiments[i])/len(categories_summaries_sentiments[i]), sum(categores_summaries_polarities[i])/len(categores_summaries_polarities[i])]
print(df_summaries)



#store df to store the sentences
#store df_summaries to store scores

    Category  Average Sentiment  Average Polarity
0       time           3.139062          3.870551
1    classes           3.094425          3.890582
2  equipment           3.096450          3.875289
3      staff           3.141156          3.868065
4      email           2.581213          3.609756


In [25]:
df
df["company_id"] = "google1"
df["industry_id"] = "1"
df["platform_id"] = "1"
df["date"] = ""



AT THIS POINT I TOOK REVIEWS AND I GOT ALL THEIR CLUSTER DATA, I ALSO HAVE DF_SUMMARIES

In [40]:
df

Sentences  \
0    I used to work here and absolutely loved my ti...   
1    Facility is too small for the number of people...   
2    It was a super friendly gym yet very crowded a...   
3    Always amazing. Using the facility  for many y...   
4    Just joined and really impressed with the clea...   
..                                                 ...   
231  Their services and rules is so bad .I called t...   
232  I had a tour.  The place looks good, but small...   
233  this is handsdown the best gym that i have eve...   
234  I used to work out here but then I found King ...   
235  I signed up with GoodLife over three months ag...   

                                   processed_sentences  \
0    used work absolutely loved time. wonderful ful...   
1    facility small number people trying serve. enf...   
2    super friendly gym yet crowded 5:30 pm. also w...   
3    always amazing. using facility many years sinc...   
4    joined really impressed cleanliness pool! swim...   
..                                                 ...   
231  services rules bad .i called stop charging wee...   
232  tour. place looks good, small. change rooms od...   
233  handsdown best gym ever joined. array great cl...   
234  used work found king cut fitness! way better r...   
235  signed goodlife three months ago hoping get ba...   

                                       bert_embeddings  cluster  Cluster  \
0    [0.32818377017974854, -0.22182533144950867, 0....       -1        1   
1    [0.1721685826778412, -0.04415113478899002, 0.1...       -1        3   
2    [0.25516438484191895, -0.31639814376831055, 0....       -1        1   
3    [-0.04373439401388168, -0.3006299138069153, 0....       -1        1   
4    [0.22954954206943512, -0.5347655415534973, 0.5...       -1        1   
..                                                 ...      ...      ...   
231  [0.24488377571105957, -0.1701994091272354, 0.6...       -1        0   
232  [0.08404839783906937, -0.26631253957748413, 0....       -1        0   
233  [0.19301766157150269, -0.07032106816768646, 0....       -1        1   
234  [0.07691993564367294, -0.42288994789123535, 0....       -1        1   
235  [0.16002558171749115, -0.2914293110370636, 0.6...       -1        2   

    assigned_label                named_labels  sentiment  polarity  \
0              [2]             [time, classes]   4.275000  4.350000   
1              [1]             [classes, time]   1.933929  3.285714   
2              [2]           [time, equipment]   3.419271  3.822917   
3              [2]      [time, staff, classes]   4.062500  4.406250   
4              [2]                      [time]   3.937500  4.083333   
..             ...                         ...        ...       ...   
231            [2]                      [time]   2.194444  3.472222   
232            [2]                      [time]   2.661651  3.635802   
233            [2]  [time, classes, equipment]   4.000000  3.953125   
234            [2]                      [time]   4.583333  4.000000   
235            [1]  [classes, time, equipment]   2.760417  3.772917   

    company_id industry_id platform_id date  
0      google1           1           1       
1      google1           1           1       
2      google1           1           1       
3      google1           1           1       
4      google1           1           1       
..         ...         ...         ...  ...  
231    google1           1           1       
232    google1           1           1       
233    google1           1           1       
234    google1           1           1       
235    google1           1           1       

[236 rows x 13 columns]

In [35]:
df_summaries['company_id'] = "google1"

In [37]:
df_summaries['industry_id'] = "1" 

In [30]:
import json
import csv
from pymongo import MongoClient
import dotenv
from dotenv import load_dotenv
import os

load_dotenv()

connection_string = os.environ.get("MONGO_URL")
client = MongoClient(connection_string)

client
# Check if authentication was successful
try:
    database_names = client.list_database_names()
    print("Authentication successful!")
except Exception as e:
    print("Authentication failed:", str(e))


Authentication successful!


Here im gonna grab the dates from the reviews and match then with the df I have rn

In [39]:
from datetime import datetime, timedelta

def generate_random_dates(start_date, end_date, n):
    """
    Generate n random dates between start_date and end_date.
    """
    start_datetime = datetime.combine(start_date, datetime.min.time())
    end_datetime = datetime.combine(end_date, datetime.min.time())
    delta = end_datetime - start_datetime
    random_dates = start_datetime + delta * np.random.rand(n)
    return [date.date() for date in random_dates]



In [41]:
start_date = datetime(2022, 1, 1).date()
end_date = datetime(2024, 5, 31).date()

num_dates = 236 # Adjust this number as needed

random_dates = generate_random_dates(start_date, end_date, num_dates)

df['date'] = random_dates

In [ ]:
df['date'] = df['date'].apply(lambda x: datetime.combine(x, datetime.min.time()))
# change to mongodb datetime.datetime instead

In [51]:

db = client['Frontend']

data = df.to_dict(orient="records")

data

[{'Sentences': "I used to work here and absolutely loved my time. It's so wonderful you have a full fledged gym, a family development centre and a daycare all in one building. The facility itself for the gym is great because there are a lot of machines you can use as well as good selection of classes to access as well depending on your needs and preference of working out. And for those parents that needed some socialising time could come by the family development centre to either be there with their kids for the programs or drop them off for child minding if they needed to use the gym.",
  'processed_sentences': 'used work absolutely loved time. wonderful full fledged gym, family development centre daycare one building. facility gym great lot machines use well good selection classes access well depending needs preference working out. parents needed socialising time could come family development centre either kids programs drop child minding needed use gym.',
  'bert_embeddings': [0.328

In [52]:

# Insert the data into MongoDB
collection = db["Reviews_testing"]

collection.insert_many(data)

InsertManyResult([ObjectId('666e027830112d3576f6b780'), ObjectId('666e027830112d3576f6b781'), ObjectId('666e027830112d3576f6b782'), ObjectId('666e027830112d3576f6b783'), ObjectId('666e027830112d3576f6b784'), ObjectId('666e027830112d3576f6b785'), ObjectId('666e027830112d3576f6b786'), ObjectId('666e027830112d3576f6b787'), ObjectId('666e027830112d3576f6b788'), ObjectId('666e027830112d3576f6b789'), ObjectId('666e027830112d3576f6b78a'), ObjectId('666e027830112d3576f6b78b'), ObjectId('666e027830112d3576f6b78c'), ObjectId('666e027830112d3576f6b78d'), ObjectId('666e027830112d3576f6b78e'), ObjectId('666e027830112d3576f6b78f'), ObjectId('666e027830112d3576f6b790'), ObjectId('666e027830112d3576f6b791'), ObjectId('666e027830112d3576f6b792'), ObjectId('666e027830112d3576f6b793'), ObjectId('666e027830112d3576f6b794'), ObjectId('666e027830112d3576f6b795'), ObjectId('666e027830112d3576f6b796'), ObjectId('666e027830112d3576f6b797'), ObjectId('666e027830112d3576f6b798'), ObjectId('666e027830112d3576f6b7